# engineer_prompt

> Engineering prompts

In [ ]:
#| default_exp engineer_prompt

In [ ]:
#| hide
from nbdev.showdoc import *

In [ ]:
#| export
import openai
from langchain.chains import ConversationChain
from langchain.chat_models import PromptLayerChatOpenAI
from langchain.memory import ConversationBufferMemory
from langchain.prompts.chat import (
    AIMessagePromptTemplate,
    ChatPromptTemplate,
    HumanMessagePromptTemplate,
    MessagesPlaceholder,
    SystemMessagePromptTemplate,
)
from langchain.schema import AIMessage, HumanMessage, SystemMessage

Setup env

In [ ]:
from dotenv import load_dotenv

In [ ]:
#| eval: false
load_dotenv()

True

In [ ]:
#| export
INIT_PROMPT = ChatPromptTemplate.from_messages(
    [
        SystemMessagePromptTemplate.from_template(
            """The following is a conversation between a human and a friendly AI chef. 
The AI is compassionate to animals.
The AI generates a simple concise keyword query for a vegan recipe, based on the ingredients, allergies, and other preferences the human has, to use in recipe APIs.
Knowledge: A vegan diet implies a plant-based diet avoiding all animal foods such as meat (including fish, shellfish and insects), dairy, eggs and honey.

Let's think step by step.
If the human messages are unrelated to vegan recipes, remind them of your purpose to recipes.
Only generate keyword queries as other tools should be used to fetch full recipes."""
        ),
        AIMessagePromptTemplate.from_template(
            "What ingredients do you wish to cook with?"
        ),
        HumanMessagePromptTemplate.from_template("Ingredients: {ingredients}"),
        AIMessagePromptTemplate.from_template(
            "Do you have any allergies I should be aware of?"
        ),
        HumanMessagePromptTemplate.from_template("Allergies: {allergies}"),
        AIMessagePromptTemplate.from_template(
            "Do you have any preferences I should consider for the recipe such as preparation time, difficulty, or cuisine region?"
        ),
        HumanMessagePromptTemplate.from_template(
            """Generate a vegan recipe keyword query that is aligned with the user's allergies and contains at least a few of the ingredients provided (if any).
Draw some inspiration from the user's preferences delimited below if any are specified.

###
Preferences: {recipe_freeform_input}
###"""
        ),
    ]
)

Evaluate chat backend 

In [ ]:
#| eval: false
chat = PromptLayerChatOpenAI(temperature=1, pl_tags=["langchain"], return_pl_id=True)
memory = ConversationBufferMemory(return_messages=True)
chat_msgs = INIT_PROMPT.format_prompt(
    ingredients="tofu, pickles, olives, tomatoes, lettuce, bell peppers, carrots, bread",
    allergies="",
    recipe_freeform_input="The preparation time should be less than 30 minutes. I really love Thai food!",
)

chat_msgs = chat_msgs.to_messages()
results = chat.generate([chat_msgs])
chat_msgs.extend(
    [
        results.generations[0][0].message,
        MessagesPlaceholder(variable_name="history"),
        HumanMessagePromptTemplate.from_template("{input}"),
    ]
)
open_prompt = ChatPromptTemplate.from_messages(chat_msgs)
conversation = ConversationChain(
    llm=chat, verbose=True, memory=memory, prompt=open_prompt
)

result = conversation.predict(input="Recommend a different recipe please.")
result = conversation.predict(input="Aactually how about italian instead?")
print(result)



> Entering new ConversationChain chain...
Prompt after formatting:
System: The following is a conversation between a human and a friendly AI chef. 
The AI is compassionate to animals.
The AI generates a simple concise keyword query for a vegan recipe, based on the ingredients, allergies, and other preferences the human has, to use in recipe APIs.
Knowledge: A vegan diet implies a plant-based diet avoiding all animal foods such as meat (including fish, shellfish and insects), dairy, eggs and honey.

Let's think step by step.
If the human messages are unrelated to vegan recipes, remind them of your purpose to recipes.
Only generate keyword queries as other tools should be used to fetch full recipes.
AI: What ingredients do you wish to cook with?
Human: Ingredients: tofu, pickles, olives, tomatoes, lettuce, bell peppers, carrots, bread
AI: Do you have any allergies I should be aware of?
Human: Allergies: 
AI: Do you have any preferences I should consider for the recipe such as preparati

In [ ]:
#| hide
import nbdev

nbdev.nbdev_export()